In [6]:
import numpy as np
from rl_env_sarl import SARLDraftEnv
import gymnasium as gym
# from stable_baselines3 import PPO
from sb3_contrib import RecurrentPPO
from stable_baselines3.common.env_checker import check_env
from pprint import pprint

In [7]:

    
def learning_rate_schedule(initial_lr=1e-4, final_lr=5e-5):
    return lambda progress_remaining: progress_remaining * (initial_lr - final_lr) + final_lr

learning_rate_schedule_fn = learning_rate_schedule(initial_lr=1e-4, final_lr=5e-5)

ppo_params = {
    "policy": "MlpLstmPolicy",
    "learning_rate": learning_rate_schedule_fn,  # Adaptive learning rate
    "n_steps": 60,  # Adjusted to be a multiple of your sequence length
    "batch_size": 256,
    "n_epochs": 15,
    "gamma": 0.99,
    "gae_lambda": 0.95,
    "clip_range": 0.2,
    "clip_range_vf": None,
    "normalize_advantage": True,
    "ent_coef": .03,  # Entropy coefficient for the loss calculation
    "vf_coef": 0.5,
    "max_grad_norm": 0.7,
    "use_sde": False,
    "sde_sample_freq": -1,
    "target_kl": 0.01,
    "stats_window_size": 100,
    "policy_kwargs": dict(
        net_arch=[dict(pi=[128, 128], vf=[128, 128])],
        n_lstm_layers=1,  # Number of LSTM layers
        lstm_hidden_size=128  # Size of the LSTM's hidden state
    ),
    "verbose": 1,
    "seed": 42,
    "device": "auto",
    "_init_setup_model": True
}

In [8]:
check_env(SARLDraftEnv())

In [9]:
# env = SARLDraftEnv()
# model = DQN(env=env, **dqn_params)
# model.learn(total_timesteps=100000)

In [10]:
import os
import json
from stable_baselines3 import PPO
from stable_baselines3.common.callbacks import BaseCallback, CheckpointCallback, EvalCallback
from stable_baselines3.common.logger import configure
from datetime import datetime

# Define your environment
env = SARLDraftEnv()

# Generate a unique run ID
run_id = datetime.now().strftime("%Y%m%d-%H%M%S")

# Choose significant parameters to include in the log directory name
lr_str = ppo_params['learning_rate'].__name__ if callable(ppo_params['learning_rate']) else ppo_params['learning_rate']
gamma_str = ppo_params['gamma'].__name__ if callable(ppo_params['gamma']) else ppo_params['gamma']
param_str = f"RNN-PPO"
# param_str = f"PPO_lr_{lr_str}_gamma_{gamma_str}"
log_dir = f"./logs/{param_str}_{run_id}/"
os.makedirs(log_dir, exist_ok=True)

# Save ppo_params to a JSON file
params_save_path = os.path.join(log_dir, f'ppo_params_{run_id}.json')
with open(params_save_path, 'w') as f:
    # if the param is not json serializable (e.g. function), then write callable name
    json_params = {key: value if not callable(value) else value.__name__ for key, value in ppo_params.items()}
    json.dump(json_params, f, indent=2)

# Configure the logger
new_logger = configure(log_dir, ["stdout", "csv", "tensorboard"])

# Define the PPO model and attach the logger
model = RecurrentPPO(**ppo_params, env=env, tensorboard_log=log_dir)
model.set_logger(new_logger)

# Log ppo_params to TensorBoard/CSV
for key, value in ppo_params.items():
    model.logger.record(f'params/{key}', value)


# Custom callback for monitoring and saving during training
class TrainingMonitorCallback(BaseCallback):
    def __init__(self, log_interval: int, save_interval: int, draft_save_interval: int, log_dir: str, run_id: str, verbose=1):
        super(TrainingMonitorCallback, self).__init__(verbose)
        self.log_interval = log_interval
        self.save_interval = save_interval
        self.draft_save_interval = draft_save_interval
        self.log_dir = log_dir
        self.run_id = run_id
        self.best_mean_reward = -float("inf")
        self.rewards_history = []
        self.losses_history = []
        self.episode_counter = 0
        self.draft_history = []  # List to store draft dicts

        self.model_save_path = os.path.join(log_dir, f'best_model_{run_id}')
        self.rewards_losses_path = os.path.join(log_dir, f'rewards_losses_{run_id}.json')
        self.drafts_save_path = os.path.join(log_dir, f'draft_history_{run_id}.json')

    def _init_callback(self) -> None:
        os.makedirs(self.log_dir, exist_ok=True)

    def _on_step(self) -> bool:
        # Log rewards
        current_reward = self.locals['rewards']
        self.rewards_history.append(current_reward)

        # Log losses if they are available (PPO does not use TD errors)
        if 'loss' in self.locals:
            current_loss = self.locals['loss']
            self.losses_history.append(current_loss)

        # Periodic logging and saving
        if self.n_calls % self.log_interval == 0:
            mean_reward = np.mean(self.rewards_history[-self.log_interval:])
            self.logger.record('mean_reward', mean_reward)

            if mean_reward > self.best_mean_reward:
                self.best_mean_reward = mean_reward
                self.model.save(self.model_save_path)
                if self.verbose > 0:
                    print(f"New best mean reward: {self.best_mean_reward}. Model saved to {self.model_save_path}")

            # Convert rewards and losses to lists before saving
            rewards_list = [float(reward.item() if isinstance(reward, np.ndarray) else reward) for reward in self.rewards_history]
            losses_list = [float(loss.item() if isinstance(loss, np.ndarray) else loss) for loss in self.losses_history]

            # Save rewards and losses to a file
            with open(self.rewards_losses_path, 'w') as f:
                json.dump({'rewards': rewards_list, 'losses': losses_list}, f)

        # Check if the episode has terminated
        if self.locals['dones'][0]:
            
            if self.episode_counter % self.draft_save_interval == 0:
                draft = self.locals['infos'][0]['draft']
                self.draft_history.append(draft)
                with open(self.drafts_save_path, 'w') as f:
                    json.dump(self.draft_history, f, indent=4)
                
            self.episode_counter += 1

        return True

# Initialize and use the custom callback
monitor_callback = TrainingMonitorCallback(log_interval=1000, save_interval=50, draft_save_interval=250, log_dir=log_dir, run_id=run_id)

# Create a checkpoint callback to save the model periodically
checkpoint_callback = CheckpointCallback(save_freq=5000, save_path=log_dir, name_prefix='ppo_model')

# Create an evaluation callback to log evaluations during training
eval_callback = EvalCallback(env, best_model_save_path=log_dir, log_path=log_dir, eval_freq=5000, deterministic=True, render=False)

# Combine all callbacks
callback = [checkpoint_callback, eval_callback, monitor_callback]

# Train the model
model.learn(total_timesteps=2e6, callback=callback)

Logging to ./logs/RNN-PPO_20240827-013859/
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/stable_baselines3/common/policies.py:486: UserWarning: As shared layers in the mlp_extractor are removed since SB3 v1.8.0, you should now pass directly a dictionary and not a list (net_arch=dict(pi=..., vf=...) instead of net_arch=[dict(pi=..., vf=...)])
  warnings.warn(


-----------------------------------------------------------------
| params/                |                                      |
|    _init_setup_model   | True                                 |
|    batch_size          | 256                                  |
|    clip_range          | 0.2                                  |
|    clip_range_vf       | None                                 |
|    device              | auto                                 |
|    ent_coef            | 0.03                                 |
|    gae_lambda          | 0.95                                 |
|    gamma               | 0.99                                 |
|    learning_rate       | <function learning_rate_schedule.... |
|    max_grad_norm       | 0.7                                  |
|    n_epochs            | 15                                   |
|    n_steps             | 60                                   |
|    normalize_advantage | True                                 |
|    polic

/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=5000, episode_reward=-0.84 +/- 0.00
Episode length: 15.00 +/- 0.00
-----------------------------------------
| eval/                   |             |
|    mean_ep_length       | 15          |
|    mean_reward          | -0.841      |
| time/                   |             |
|    total_timesteps      | 5000        |
| train/                  |             |
|    approx_kl            | 0.009225871 |
|    clip_fraction        | 0.0189      |
|    clip_range           | 0.2         |
|    entropy_loss         | -1.62       |
|    explained_variance   | 0.607       |
|    learning_rate        | 9.99e-05    |
|    loss                 | -0.067      |
|    n_updates            | 1245        |
|    policy_gradient_loss | -0.0123     |
|    value_loss           | 0.0637      |
-----------------------------------------
New best mean reward!
New best mean reward: -0.012029980309307575. Model saved to ./logs/RNN-PPO_20240827-013859/best_model_20240827-013859
------------------

...

/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=415000, episode_reward=0.83 +/- 0.01
Episode length: 15.00 +/- 0.00
-----------------------------------------
| eval/                   |             |
|    mean_ep_length       | 15          |
|    mean_reward          | 0.833       |
| time/                   |             |
|    total_timesteps      | 415000      |
| train/                  |             |
|    approx_kl            | 0.005096938 |
|    clip_fraction        | 0.0278      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.292      |
|    explained_variance   | 0.995       |
|    learning_rate        | 8.96e-05    |
|    loss                 | -0.026      |
|    n_updates            | 103740      |
|    policy_gradient_loss | -0.00887    |
|    value_loss           | 7.03e-05    |
-----------------------------------------
------------------------------------
| mean_reward        | 0.053639594 |
| rollout/           |             |
|    ep_len_mean     | 15.1        |
|    ep_r

/Users/ashish/files/fun_projects/fantasy_football_2024/venv/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=420000, episode_reward=0.83 +/- 0.01
Episode length: 15.00 +/- 0.00
-----------------------------------------
| eval/                   |             |
|    mean_ep_length       | 15          |
|    mean_reward          | 0.828       |
| time/                   |             |
|    total_timesteps      | 420000      |
| train/                  |             |
|    approx_kl            | 0.015625969 |
|    clip_fraction        | 0.0405      |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.29       |
|    explained_variance   | 0.989       |
|    learning_rate        | 8.95e-05    |
|    loss                 | -0.0432     |
|    n_updates            | 104985      |
|    policy_gradient_loss | -0.0209     |
|    value_loss           | 0.000139    |
-----------------------------------------
-----------------------------------
| mean_reward        | 0.05493687 |
| rollout/           |            |
|    ep_len_mean     | 15         |
|    ep_rew_m

KeyboardInterrupt: 